In [1]:
import Bio

In [1]:
#!/usr/bin/python3 
from hyperparams import *
from rawdata_preprocessing import read_RPI_pairSeq, read_NPInter_pairSeq
from copy import deepcopy
import numpy as np

isPrint = True

# Reduced Protein letters(7 letters)
def get_reduced_protein_letter_dict():
    rpdict = {}
    reduced_letters = [["A","G","V"],
                       ["I","L","F","P"],
                       ["Y","M","T","S"],
                       ["H","N","Q","W"],
                       ["R","K"],
                       ["D","E"],
                       ["C"]]
    changed_letter = ["A","B","C","D","E","F","G"]
    for class_idx, class_letters in enumerate(reduced_letters):
        for letter in class_letters:
            rpdict[letter] = changed_letter[class_idx]
    
    return rpdict

# Improved CTF 
class improvedCTF:
    def __init__(self, letters, length):
        self.letters = letters
        self.length = length
        self.dict = {}
        self.generate_feature_dict()
        
    def generate_feature_dict(self):
        def generate(cur_key, depth):
            if depth == self.length:
                return
            for k in self.letters:
                next_key = cur_key + k
                self.dict[next_key] = 0
                generate(next_key, depth+1)
                
        generate(cur_key="",depth=0)
        
        if isPrint:
            print("iterate letters : {}".format(self.letters))
            print("number of keys  : {}".format(len(self.dict.keys())))
        
    
    def get_feature_dict(self):
        for k in self.dict.keys():
            self.dict[k] = 0
            
        return deepcopy(self.dict)

    
# CTF feature processing
def preprocess_feature(x, y, npz_path):
    
    def min_max_norm(a):
        a_min = np.min(a)
        a_max = np.max(a)
        return (a - a_min)/(a_max - a_min)
    
    rpdict = get_reduced_protein_letter_dict()
    feature_x = []
    r_mer = 4
    r_CTF = improvedCTF(letters=["A","C","G","U"],length=r_mer)
    #r_feature_dict = r_CTF.get_feature_dict()
    
    p_mer = 3
    p_CTF = improvedCTF(letters=["A","B","C","D","E","F","G"],length=p_mer)
    #p_feature_dict = p_CTF.get_feature_dict()
    
    x_protein = []
    x_rna = []
        
    for idx, (pseq, rseq) in enumerate(x):
        
        r_feature_dict = r_CTF.get_feature_dict()
        p_feature_dict = p_CTF.get_feature_dict()
        rpseq = []
        for p in pseq:
            if p=="X": 
                rpseq.append(p)
            else:
                rpseq.append(rpdict[p])
                
        pseq = rpseq
        temp_pseq = ""
        for p in pseq:
            temp_pseq += p
        pseq = temp_pseq
        
        for mer in range(1,p_mer+1):
            for i in range(0,len(pseq)-mer):
                pattern = pseq[i:i+mer]
                try:
                    p_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        
        for mer in range(1,r_mer+1):
            for i in range(0,len(rseq)-mer):
                pattern = rseq[i:i+mer]
                try:
                    r_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        
        
        
        p_feature = np.array(list(p_feature_dict.values()))
        p_feature = min_max_norm(p_feature)
        
        r_feature = np.array(list(r_feature_dict.values()))
        r_feature = min_max_norm(r_feature)
        
        x_protein.append(p_feature)
        x_rna.append(r_feature)
        
        if isPrint : 
            print("CTF preprocessing ({} / {})".format(idx+1, len(x)))
            #print(r_feature)
            
                
    
    x_protein = np.array(x_protein)
    x_rna = np.array(x_rna)
    y = np.array(y)
    np.savez(npz_path,XP=x_protein, XR=x_rna, Y=y)
    
    if isPrint :
        print("Protein feature : {}".format(x_protein.shape))
        print("RNA feature     : {}".format(x_rna.shape))
        print("Labels          : {}".format(y.shape))
        print("Saved path      : {}".format(npz_path))
    
     
    return x_protein, x_rna, y

def preprocess_and_savez_NPInter():
    X, Y = read_NPInter_pairSeq()
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["NPInter"])
    
def preprocess_and_savez_RPI(size):
    X, Y = read_RPI_pairSeq(size)
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["RPI"][size])

if __name__ == "__main__":
    print("Feature Preprocessing")
    preprocess_and_savez_NPInter()
    preprocess_and_savez_RPI(1807)
    preprocess_and_savez_RPI(2241)
    preprocess_and_savez_RPI(369)
    preprocess_and_savez_RPI(488)
    
    
    
    

Feature Preprocessing
iterate letters : ['A', 'C', 'G', 'U']
number of keys  : 340
iterate letters : ['A', 'B', 'C', 'D', 'E', 'F', 'G']
number of keys  : 399
CTF preprocessing (1 / 20824)
CTF preprocessing (2 / 20824)
CTF preprocessing (3 / 20824)
CTF preprocessing (4 / 20824)
CTF preprocessing (5 / 20824)
CTF preprocessing (6 / 20824)
CTF preprocessing (7 / 20824)
CTF preprocessing (8 / 20824)
CTF preprocessing (9 / 20824)
CTF preprocessing (10 / 20824)
CTF preprocessing (11 / 20824)
CTF preprocessing (12 / 20824)
CTF preprocessing (13 / 20824)
CTF preprocessing (14 / 20824)
CTF preprocessing (15 / 20824)
CTF preprocessing (16 / 20824)
CTF preprocessing (17 / 20824)
CTF preprocessing (18 / 20824)
CTF preprocessing (19 / 20824)
CTF preprocessing (20 / 20824)
CTF preprocessing (21 / 20824)
CTF preprocessing (22 / 20824)
CTF preprocessing (23 / 20824)
CTF preprocessing (24 / 20824)
CTF preprocessing (25 / 20824)
CTF preprocessing (26 / 20824)
CTF preprocessing (27 / 20824)
CTF preproces

CTF preprocessing (276 / 20824)
CTF preprocessing (277 / 20824)
CTF preprocessing (278 / 20824)
CTF preprocessing (279 / 20824)
CTF preprocessing (280 / 20824)
CTF preprocessing (281 / 20824)
CTF preprocessing (282 / 20824)
CTF preprocessing (283 / 20824)
CTF preprocessing (284 / 20824)
CTF preprocessing (285 / 20824)
CTF preprocessing (286 / 20824)
CTF preprocessing (287 / 20824)
CTF preprocessing (288 / 20824)
CTF preprocessing (289 / 20824)
CTF preprocessing (290 / 20824)
CTF preprocessing (291 / 20824)
CTF preprocessing (292 / 20824)
CTF preprocessing (293 / 20824)
CTF preprocessing (294 / 20824)
CTF preprocessing (295 / 20824)
CTF preprocessing (296 / 20824)
CTF preprocessing (297 / 20824)
CTF preprocessing (298 / 20824)
CTF preprocessing (299 / 20824)
CTF preprocessing (300 / 20824)
CTF preprocessing (301 / 20824)
CTF preprocessing (302 / 20824)
CTF preprocessing (303 / 20824)
CTF preprocessing (304 / 20824)
CTF preprocessing (305 / 20824)
CTF preprocessing (306 / 20824)
CTF prep

CTF preprocessing (560 / 20824)
CTF preprocessing (561 / 20824)
CTF preprocessing (562 / 20824)
CTF preprocessing (563 / 20824)
CTF preprocessing (564 / 20824)
CTF preprocessing (565 / 20824)
CTF preprocessing (566 / 20824)
CTF preprocessing (567 / 20824)
CTF preprocessing (568 / 20824)
CTF preprocessing (569 / 20824)
CTF preprocessing (570 / 20824)
CTF preprocessing (571 / 20824)
CTF preprocessing (572 / 20824)
CTF preprocessing (573 / 20824)
CTF preprocessing (574 / 20824)
CTF preprocessing (575 / 20824)
CTF preprocessing (576 / 20824)
CTF preprocessing (577 / 20824)
CTF preprocessing (578 / 20824)
CTF preprocessing (579 / 20824)
CTF preprocessing (580 / 20824)
CTF preprocessing (581 / 20824)
CTF preprocessing (582 / 20824)
CTF preprocessing (583 / 20824)
CTF preprocessing (584 / 20824)
CTF preprocessing (585 / 20824)
CTF preprocessing (586 / 20824)
CTF preprocessing (587 / 20824)
CTF preprocessing (588 / 20824)
CTF preprocessing (589 / 20824)
CTF preprocessing (590 / 20824)
CTF prep

CTF preprocessing (827 / 20824)
CTF preprocessing (828 / 20824)
CTF preprocessing (829 / 20824)
CTF preprocessing (830 / 20824)
CTF preprocessing (831 / 20824)
CTF preprocessing (832 / 20824)
CTF preprocessing (833 / 20824)
CTF preprocessing (834 / 20824)
CTF preprocessing (835 / 20824)
CTF preprocessing (836 / 20824)
CTF preprocessing (837 / 20824)
CTF preprocessing (838 / 20824)
CTF preprocessing (839 / 20824)
CTF preprocessing (840 / 20824)
CTF preprocessing (841 / 20824)
CTF preprocessing (842 / 20824)
CTF preprocessing (843 / 20824)
CTF preprocessing (844 / 20824)
CTF preprocessing (845 / 20824)
CTF preprocessing (846 / 20824)
CTF preprocessing (847 / 20824)
CTF preprocessing (848 / 20824)
CTF preprocessing (849 / 20824)
CTF preprocessing (850 / 20824)
CTF preprocessing (851 / 20824)
CTF preprocessing (852 / 20824)
CTF preprocessing (853 / 20824)
CTF preprocessing (854 / 20824)
CTF preprocessing (855 / 20824)
CTF preprocessing (856 / 20824)
CTF preprocessing (857 / 20824)
CTF prep

CTF preprocessing (1085 / 20824)
CTF preprocessing (1086 / 20824)
CTF preprocessing (1087 / 20824)
CTF preprocessing (1088 / 20824)
CTF preprocessing (1089 / 20824)
CTF preprocessing (1090 / 20824)
CTF preprocessing (1091 / 20824)
CTF preprocessing (1092 / 20824)
CTF preprocessing (1093 / 20824)
CTF preprocessing (1094 / 20824)
CTF preprocessing (1095 / 20824)
CTF preprocessing (1096 / 20824)
CTF preprocessing (1097 / 20824)
CTF preprocessing (1098 / 20824)
CTF preprocessing (1099 / 20824)
CTF preprocessing (1100 / 20824)
CTF preprocessing (1101 / 20824)
CTF preprocessing (1102 / 20824)
CTF preprocessing (1103 / 20824)
CTF preprocessing (1104 / 20824)
CTF preprocessing (1105 / 20824)
CTF preprocessing (1106 / 20824)
CTF preprocessing (1107 / 20824)
CTF preprocessing (1108 / 20824)
CTF preprocessing (1109 / 20824)
CTF preprocessing (1110 / 20824)
CTF preprocessing (1111 / 20824)
CTF preprocessing (1112 / 20824)
CTF preprocessing (1113 / 20824)
CTF preprocessing (1114 / 20824)
CTF prepro

...

CTF preprocessing (4328 / 4482)
CTF preprocessing (4329 / 4482)
CTF preprocessing (4330 / 4482)
CTF preprocessing (4331 / 4482)
CTF preprocessing (4332 / 4482)
CTF preprocessing (4333 / 4482)
CTF preprocessing (4334 / 4482)
CTF preprocessing (4335 / 4482)
CTF preprocessing (4336 / 4482)
CTF preprocessing (4337 / 4482)
CTF preprocessing (4338 / 4482)
CTF preprocessing (4339 / 4482)
CTF preprocessing (4340 / 4482)
CTF preprocessing (4341 / 4482)
CTF preprocessing (4342 / 4482)
CTF preprocessing (4343 / 4482)
CTF preprocessing (4344 / 4482)
CTF preprocessing (4345 / 4482)
CTF preprocessing (4346 / 4482)
CTF preprocessing (4347 / 4482)
CTF preprocessing (4348 / 4482)
CTF preprocessing (4349 / 4482)
CTF preprocessing (4350 / 4482)
CTF preprocessing (4351 / 4482)
CTF preprocessing (4352 / 4482)
CTF preprocessing (4353 / 4482)
CTF preprocessing (4354 / 4482)
CTF preprocessing (4355 / 4482)
CTF preprocessing (4356 / 4482)
CTF preprocessing (4357 / 4482)
CTF preprocessing (4358 / 4482)
CTF prep

CTF preprocessing (117 / 738)
CTF preprocessing (118 / 738)
CTF preprocessing (119 / 738)
CTF preprocessing (120 / 738)
CTF preprocessing (121 / 738)
CTF preprocessing (122 / 738)
CTF preprocessing (123 / 738)
CTF preprocessing (124 / 738)
CTF preprocessing (125 / 738)
CTF preprocessing (126 / 738)
CTF preprocessing (127 / 738)
CTF preprocessing (128 / 738)
CTF preprocessing (129 / 738)
CTF preprocessing (130 / 738)
CTF preprocessing (131 / 738)
CTF preprocessing (132 / 738)
CTF preprocessing (133 / 738)
CTF preprocessing (134 / 738)
CTF preprocessing (135 / 738)
CTF preprocessing (136 / 738)
CTF preprocessing (137 / 738)
CTF preprocessing (138 / 738)
CTF preprocessing (139 / 738)
CTF preprocessing (140 / 738)
CTF preprocessing (141 / 738)
CTF preprocessing (142 / 738)
CTF preprocessing (143 / 738)
CTF preprocessing (144 / 738)
CTF preprocessing (145 / 738)
CTF preprocessing (146 / 738)
CTF preprocessing (147 / 738)
CTF preprocessing (148 / 738)
CTF preprocessing (149 / 738)
CTF prepro

CTF preprocessing (395 / 738)
CTF preprocessing (396 / 738)
CTF preprocessing (397 / 738)
CTF preprocessing (398 / 738)
CTF preprocessing (399 / 738)
CTF preprocessing (400 / 738)
CTF preprocessing (401 / 738)
CTF preprocessing (402 / 738)
CTF preprocessing (403 / 738)
CTF preprocessing (404 / 738)
CTF preprocessing (405 / 738)
CTF preprocessing (406 / 738)
CTF preprocessing (407 / 738)
CTF preprocessing (408 / 738)
CTF preprocessing (409 / 738)
CTF preprocessing (410 / 738)
CTF preprocessing (411 / 738)
CTF preprocessing (412 / 738)
CTF preprocessing (413 / 738)
CTF preprocessing (414 / 738)
CTF preprocessing (415 / 738)
CTF preprocessing (416 / 738)
CTF preprocessing (417 / 738)
CTF preprocessing (418 / 738)
CTF preprocessing (419 / 738)
CTF preprocessing (420 / 738)
CTF preprocessing (421 / 738)
CTF preprocessing (422 / 738)
CTF preprocessing (423 / 738)
CTF preprocessing (424 / 738)
CTF preprocessing (425 / 738)
CTF preprocessing (426 / 738)
CTF preprocessing (427 / 738)
CTF prepro

CTF preprocessing (679 / 738)
CTF preprocessing (680 / 738)
CTF preprocessing (681 / 738)
CTF preprocessing (682 / 738)
CTF preprocessing (683 / 738)
CTF preprocessing (684 / 738)
CTF preprocessing (685 / 738)
CTF preprocessing (686 / 738)
CTF preprocessing (687 / 738)
CTF preprocessing (688 / 738)
CTF preprocessing (689 / 738)
CTF preprocessing (690 / 738)
CTF preprocessing (691 / 738)
CTF preprocessing (692 / 738)
CTF preprocessing (693 / 738)
CTF preprocessing (694 / 738)
CTF preprocessing (695 / 738)
CTF preprocessing (696 / 738)
CTF preprocessing (697 / 738)
CTF preprocessing (698 / 738)
CTF preprocessing (699 / 738)
CTF preprocessing (700 / 738)
CTF preprocessing (701 / 738)
CTF preprocessing (702 / 738)
CTF preprocessing (703 / 738)
CTF preprocessing (704 / 738)
CTF preprocessing (705 / 738)
CTF preprocessing (706 / 738)
CTF preprocessing (707 / 738)
CTF preprocessing (708 / 738)
CTF preprocessing (709 / 738)
CTF preprocessing (710 / 738)
CTF preprocessing (711 / 738)
CTF prepro

CTF preprocessing (236 / 488)
CTF preprocessing (237 / 488)
CTF preprocessing (238 / 488)
CTF preprocessing (239 / 488)
CTF preprocessing (240 / 488)
CTF preprocessing (241 / 488)
CTF preprocessing (242 / 488)
CTF preprocessing (243 / 488)
CTF preprocessing (244 / 488)
CTF preprocessing (245 / 488)
CTF preprocessing (246 / 488)
CTF preprocessing (247 / 488)
CTF preprocessing (248 / 488)
CTF preprocessing (249 / 488)
CTF preprocessing (250 / 488)
CTF preprocessing (251 / 488)
CTF preprocessing (252 / 488)
CTF preprocessing (253 / 488)
CTF preprocessing (254 / 488)
CTF preprocessing (255 / 488)
CTF preprocessing (256 / 488)
CTF preprocessing (257 / 488)
CTF preprocessing (258 / 488)
CTF preprocessing (259 / 488)
CTF preprocessing (260 / 488)
CTF preprocessing (261 / 488)
CTF preprocessing (262 / 488)
CTF preprocessing (263 / 488)
CTF preprocessing (264 / 488)
CTF preprocessing (265 / 488)
CTF preprocessing (266 / 488)
CTF preprocessing (267 / 488)
CTF preprocessing (268 / 488)
CTF prepro

In [2]:
data = load('./npz/RPI369.npz')
print(data)

NameError: name 'load' is not defined

In [3]:
data = np.load('./npz/RPI369.npz')
print(data)

In [4]:
data = load('./npz/RPI369.npz')
data

NameError: name 'load' is not defined

In [5]:
data = np.load('./npz/RPI369.npz')
print(data)

In [6]:
data = np.load('./npz/RPI369.npz')
data

In [7]:
dataset-name = data['dataset-name']

SyntaxError: can't assign to operator (<ipython-input-7-11b33a3dd003>, line 1)

In [8]:
data0 = data['0']

KeyError: '0 is not a file in the archive'

In [9]:
data

In [10]:
mydata = np.load('./npz/RPI369.npz')
mydata

In [11]:
mydata_database = mydata['database']
mydata_database

KeyError: 'database is not a file in the archive'

In [12]:
mydata[1, :]

TypeError: not all arguments converted during string formatting

In [13]:
xp_mydata = mydata['XP']
xp_mydata

array([[0.51851852, 0.03703704, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.74916388, 0.09364548, 0.01672241, ..., 0.        , 0.        ,
        0.        ],
       [0.78199052, 0.15876777, 0.02132701, ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.42424242, 0.04545455, 0.01515152, ..., 0.        , 0.        ,
        0.        ],
       [0.57142857, 0.06122449, 0.01020408, ..., 0.        , 0.        ,
        0.        ],
       [1.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [14]:
    np.savez(npz_path,XP=x_protein, XR=x_rna, Y=y)

NameError: name 'npz_path' is not defined

In [15]:
xr_mydata = mydata['XR']
y_mydata = mydata['Y']
xr_mydata
printf("------------")
y_mydata

NameError: name 'printf' is not defined

In [16]:
xr_mydata = mydata['XR']
y_mydata = mydata['Y']
xr_mydata
print("------------")
y_mydata

------------


array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [17]:
xr_mydata

array([[0.4       , 0.08      , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.57142857, 0.14285714, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.57142857, 0.14285714, 0.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.83333333, 0.16666667, 0.        , ..., 0.        , 0.16666667,
        0.        ],
       [0.58333333, 0.125     , 0.08333333, ..., 0.        , 0.        ,
        0.        ],
       [0.5       , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [18]:
len(xr_mydata)

738

In [19]:
xr_mydata[1]

array([0.57142857, 0.14285714, 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.14285714, 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.42857143,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.14285714, 0.        , 0.        , 0.14285714, 0.     

In [20]:
len(xr_mydata[1])

340

In [21]:
len(GGCCGGCAUGGUCCCAGCCUCCUCGCUGGCGCCGGCUGGGCAACACCAUUGCACUCCGGUGGCGAAUGGGAC)

NameError: name 'GGCCGGCAUGGUCCCAGCCUCCUCGCUGGCGCCGGCUGGGCAACACCAUUGCACUCCGGUGGCGAAUGGGAC' is not defined

In [22]:
len('GGCCGGCAUGGUCCCAGCCUCCUCGCUGGCGCCGGCUGGGCAACACCAUUGCACUCCGGUGGCGAAUGGGAC')

72

In [23]:
len('AUACUUACCUGGCAGGGGAGAUACCAUGAUCACGAAGGUGGUUUUCCCAGGGGAGACGUCCCCUGCGAUUUCCCCAAAUGUGGGAAACUCGACUGCAUAAUUUGUGGUAGUGGGGGACUGCGUUCGCGCUUUCCCCUG')

138

In [24]:
y_data

NameError: name 'y_data' is not defined

In [25]:
y_mydata

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [26]:
len(y_mydata)

738

In [27]:
y_mydata[737]

0

In [32]:
#!/usr/bin/python3 
from hyperparams import *
from rawdata_preprocessing import read_RPI_pairSeq, read_NPInter_pairSeq
from copy import deepcopy
import numpy as np

isPrint = True

# Reduced Protein letters(7 letters)
def get_reduced_protein_letter_dict():
    rpdict = {}
    reduced_letters = [["A","G","V"],
                       ["I","L","F","P"],
                       ["Y","M","T","S"],
                       ["H","N","Q","W"],
                       ["R","K"],
                       ["D","E"],
                       ["C"]]
    changed_letter = ["A","B","C","D","E","F","G"]
    for class_idx, class_letters in enumerate(reduced_letters):
        for letter in class_letters:
            rpdict[letter] = changed_letter[class_idx]
    
    return rpdict

# Improved CTF 
class improvedCTF:
    def __init__(self, letters, length):
        self.letters = letters
        self.length = length
        self.dict = {}
        self.generate_feature_dict()
        
    def generate_feature_dict(self):
        def generate(cur_key, depth):
            if depth == self.length:
                return
            for k in self.letters:
                next_key = cur_key + k
                self.dict[next_key] = 0
                generate(next_key, depth+1)
                
        generate(cur_key="",depth=0)
        
        if isPrint:
            print("iterate letters : {}".format(self.letters))
            print("number of keys  : {}".format(len(self.dict.keys())))
        
    
    def get_feature_dict(self):
        for k in self.dict.keys():
            self.dict[k] = 0
            
        return deepcopy(self.dict)

    
# CTF feature processing
def preprocess_feature(x, y, npz_path):
    
    def min_max_norm(a):
        a_min = np.min(a)
        a_max = np.max(a)
        return (a - a_min)/(a_max - a_min)
    
    rpdict = get_reduced_protein_letter_dict()
    feature_x = []
    r_mer = 4
    r_CTF = improvedCTF(letters=["A","C","G","U"],length=r_mer)
    #r_feature_dict = r_CTF.get_feature_dict()
    print("r_CTF : ", r_CTF)
    print("r_CTF.get_feature_dict() : ", r_CTF.get_feature_dict())
    
    p_mer = 3
    p_CTF = improvedCTF(letters=["A","B","C","D","E","F","G"],length=p_mer)
    #p_feature_dict = p_CTF.get_feature_dict()
    print("p_CTF : ", p_CTF)
    print("p_CTF.get_feature_dict() : ", p_CTF.get_feature_dict())
    
    x_protein = []
    x_rna = []
    
    return;
        
    for idx, (pseq, rseq) in enumerate(x):
        
        r_feature_dict = r_CTF.get_feature_dict()
        p_feature_dict = p_CTF.get_feature_dict()
        rpseq = []
        for p in pseq:
            if p=="X": 
                rpseq.append(p)
            else:
                rpseq.append(rpdict[p])
                
        pseq = rpseq
        temp_pseq = ""
        for p in pseq:
            temp_pseq += p
        pseq = temp_pseq
        
        for mer in range(1,p_mer+1):
            for i in range(0,len(pseq)-mer):
                pattern = pseq[i:i+mer]
                try:
                    p_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        
        for mer in range(1,r_mer+1):
            for i in range(0,len(rseq)-mer):
                pattern = rseq[i:i+mer]
                try:
                    r_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        
        
        
        p_feature = np.array(list(p_feature_dict.values()))
        p_feature = min_max_norm(p_feature)
        
        r_feature = np.array(list(r_feature_dict.values()))
        r_feature = min_max_norm(r_feature)
        
        x_protein.append(p_feature)
        x_rna.append(r_feature)
        
        if isPrint : 
            print("CTF preprocessing ({} / {})".format(idx+1, len(x)))
            #print(r_feature)
            
                
    
    x_protein = np.array(x_protein)
    x_rna = np.array(x_rna)
    y = np.array(y)
    np.savez(npz_path,XP=x_protein, XR=x_rna, Y=y)
    
    if isPrint :
        print("Protein feature : {}".format(x_protein.shape))
        print("RNA feature     : {}".format(x_rna.shape))
        print("Labels          : {}".format(y.shape))
        print("Saved path      : {}".format(npz_path))
    
     
    return x_protein, x_rna, y

def preprocess_and_savez_NPInter():
    X, Y = read_NPInter_pairSeq()
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["NPInter"])
    
def preprocess_and_savez_RPI(size):
    X, Y = read_RPI_pairSeq(size)
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["RPI"][size])

if __name__ == "__main__":
    print("Feature Preprocessing")
    #preprocess_and_savez_NPInter()
    #preprocess_and_savez_RPI(1807)
    #preprocess_and_savez_RPI(2241)
    preprocess_and_savez_RPI(369)
    #preprocess_and_savez_RPI(488)
    
    
    
    

Feature Preprocessing
iterate letters : ['A', 'C', 'G', 'U']
number of keys  : 340
r_CTF :  <__main__.improvedCTF object at 0x0000028515C8C7C8>
r_CTF.get_feature_dict() :  {'A': 0, 'AA': 0, 'AAA': 0, 'AAAA': 0, 'AAAC': 0, 'AAAG': 0, 'AAAU': 0, 'AAC': 0, 'AACA': 0, 'AACC': 0, 'AACG': 0, 'AACU': 0, 'AAG': 0, 'AAGA': 0, 'AAGC': 0, 'AAGG': 0, 'AAGU': 0, 'AAU': 0, 'AAUA': 0, 'AAUC': 0, 'AAUG': 0, 'AAUU': 0, 'AC': 0, 'ACA': 0, 'ACAA': 0, 'ACAC': 0, 'ACAG': 0, 'ACAU': 0, 'ACC': 0, 'ACCA': 0, 'ACCC': 0, 'ACCG': 0, 'ACCU': 0, 'ACG': 0, 'ACGA': 0, 'ACGC': 0, 'ACGG': 0, 'ACGU': 0, 'ACU': 0, 'ACUA': 0, 'ACUC': 0, 'ACUG': 0, 'ACUU': 0, 'AG': 0, 'AGA': 0, 'AGAA': 0, 'AGAC': 0, 'AGAG': 0, 'AGAU': 0, 'AGC': 0, 'AGCA': 0, 'AGCC': 0, 'AGCG': 0, 'AGCU': 0, 'AGG': 0, 'AGGA': 0, 'AGGC': 0, 'AGGG': 0, 'AGGU': 0, 'AGU': 0, 'AGUA': 0, 'AGUC': 0, 'AGUG': 0, 'AGUU': 0, 'AU': 0, 'AUA': 0, 'AUAA': 0, 'AUAC': 0, 'AUAG': 0, 'AUAU': 0, 'AUC': 0, 'AUCA': 0, 'AUCC': 0, 'AUCG': 0, 'AUCU': 0, 'AUG': 0, 'AUGA': 0, 'AUGC'

TypeError: cannot unpack non-iterable NoneType object

In [42]:
#!/usr/bin/python3 
from hyperparams import *
from rawdata_preprocessing import read_RPI_pairSeq, read_NPInter_pairSeq
from copy import deepcopy
import numpy as np

isPrint = True

# Reduced Protein letters(7 letters)
def get_reduced_protein_letter_dict():
    rpdict = {}
    reduced_letters = [["A","G","V"],
                       ["I","L","F","P"],
                       ["Y","M","T","S"],
                       ["H","N","Q","W"],
                       ["R","K"],
                       ["D","E"],
                       ["C"]]
    changed_letter = ["A","B","C","D","E","F","G"]
    for class_idx, class_letters in enumerate(reduced_letters):
        for letter in class_letters:
            rpdict[letter] = changed_letter[class_idx]
                
    #rpdict = {"A" : ["A","G","V"], "B" : ["I","L","F","P"], ... }
    return rpdict

# Improved CTF 
class improvedCTF:
    def __init__(self, letters, length):
        self.letters = letters
        self.length = length
        self.dict = {}
        self.generate_feature_dict()
        
    def generate_feature_dict(self):
        def generate(cur_key, depth):
            if depth == self.length:
                return
            for k in self.letters:
                next_key = cur_key + k
                self.dict[next_key] = 0
                generate(next_key, depth+1)
                
        generate(cur_key="",depth=0)
        
        if isPrint:
            print("iterate letters : {}".format(self.letters))
            print("number of keys  : {}".format(len(self.dict.keys())))
        
    
    def get_feature_dict(self):
        for k in self.dict.keys():
            self.dict[k] = 0
            
        return deepcopy(self.dict)

    
# CTF feature processing
def preprocess_feature(x, y, npz_path): # /data/npz/RPI369.npz 파일을 생성하는 함수.
# read_RPI_pairSeq(size) 의 return값 X, Y가 각각 x, y
# X : 2차원 배열 [[protein value1, rna value1], [protein value2, rna value2], ... ]
# Y : 1차원 배열. label의 배열 [1, 1, 1, ... , 0, 0, 0]
    
    def min_max_norm(a):
        a_min = np.min(a)
        a_max = np.max(a)
        return (a - a_min)/(a_max - a_min)
    
    rpdict = get_reduced_protein_letter_dict()
    feature_x = []
    r_mer = 4
    r_CTF = improvedCTF(letters=["A","C","G","U"],length=r_mer)
    #r_feature_dict = r_CTF.get_feature_dict()
    
    p_mer = 3
    p_CTF = improvedCTF(letters=["A","B","C","D","E","F","G"],length=p_mer)
    #p_feature_dict = p_CTF.get_feature_dict()
    
    x_protein = []
    x_rna = []
        
    for idx, (pseq, rseq) in enumerate(x): # pseq : protein value / rseq : RNA value
        
        r_feature_dict = r_CTF.get_feature_dict()
        p_feature_dict = p_CTF.get_feature_dict()
        print("p_feature_dict : ", p_feature_dict)
        rpseq = []
        print("pseq : ", pseq)
        for p in pseq: # MQKGNFRNQRKTVKCFNCGKEGHIAKNCRAPRKKGCWKCGKEGHQMKDCTERQANX 의 각 알파벳을 p로 받으면서 순회한다.
            if p=="X": # MQKGNFRNQRKTVKCFNCGKEGHIAKNCRAPRKKGCWKCGKEGHQMKDCTERQANX 에서 X가 포함되어 있으면 ~?
                rpseq.append(p)
            else:
                rpseq.append(rpdict[p])
        print("rpseq : ", rpseq)
        
                
        pseq = rpseq
        temp_pseq = ""
        for p in pseq:
            temp_pseq += p
        pseq = temp_pseq
        print("temp_pseq : ", temp_pseq)
        
        for mer in range(1,p_mer+1):
            for i in range(0,len(pseq)-mer):
                pattern = pseq[i:i+mer]
                try:
                    p_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        
        for mer in range(1,r_mer+1):
            for i in range(0,len(rseq)-mer):
                pattern = rseq[i:i+mer]
                try:
                    r_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        #print("p_feature_dict : ", p_feature_dict)
        #print("r_feature_dict : ", r_feature_dict)
        
        
        p_feature = np.array(list(p_feature_dict.values()))
        print("p_feature before min_max_norm : ", p_feature)
        p_feature = min_max_norm(p_feature)
        print("p_feature : ", p_feature)
        
        r_feature = np.array(list(r_feature_dict.values()))
        print("r_feature before min_max_norm : ", r_feature)
        r_feature = min_max_norm(r_feature)
        print("r_feature : ", r_feature)
        
        x_protein.append(p_feature)
        x_rna.append(r_feature)
        
        if isPrint : 
            print("CTF preprocessing ({} / {})".format(idx+1, len(x)))
            #print(r_feature)
        return 0;   
                
    
    x_protein = np.array(x_protein)
    x_rna = np.array(x_rna)
    y = np.array(y)
    np.savez(npz_path,XP=x_protein, XR=x_rna, Y=y)
    
    if isPrint :
        print("Protein feature : {}".format(x_protein.shape))
        print("RNA feature     : {}".format(x_rna.shape))
        print("Labels          : {}".format(y.shape))
        print("Saved path      : {}".format(npz_path))
    
        
    return x_protein, x_rna, y

def preprocess_and_savez_NPInter():
    X, Y = read_NPInter_pairSeq()
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["NPInter"])
    
def preprocess_and_savez_RPI(size):
    X, Y = read_RPI_pairSeq(size)
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["RPI"][size])

if __name__ == "__main__":
    print("Feature Preprocessing")
    #preprocess_and_savez_NPInter()
    #preprocess_and_savez_RPI(1807)
    #preprocess_and_savez_RPI(2241)
    preprocess_and_savez_RPI(369)
    #preprocess_and_savez_RPI(488)
    
    
    
    

Feature Preprocessing
iterate letters : ['A', 'C', 'G', 'U']
number of keys  : 340
iterate letters : ['A', 'B', 'C', 'D', 'E', 'F', 'G']
number of keys  : 399
p_feature_dict :  {'A': 0, 'AA': 0, 'AAA': 0, 'AAB': 0, 'AAC': 0, 'AAD': 0, 'AAE': 0, 'AAF': 0, 'AAG': 0, 'AB': 0, 'ABA': 0, 'ABB': 0, 'ABC': 0, 'ABD': 0, 'ABE': 0, 'ABF': 0, 'ABG': 0, 'AC': 0, 'ACA': 0, 'ACB': 0, 'ACC': 0, 'ACD': 0, 'ACE': 0, 'ACF': 0, 'ACG': 0, 'AD': 0, 'ADA': 0, 'ADB': 0, 'ADC': 0, 'ADD': 0, 'ADE': 0, 'ADF': 0, 'ADG': 0, 'AE': 0, 'AEA': 0, 'AEB': 0, 'AEC': 0, 'AED': 0, 'AEE': 0, 'AEF': 0, 'AEG': 0, 'AF': 0, 'AFA': 0, 'AFB': 0, 'AFC': 0, 'AFD': 0, 'AFE': 0, 'AFF': 0, 'AFG': 0, 'AG': 0, 'AGA': 0, 'AGB': 0, 'AGC': 0, 'AGD': 0, 'AGE': 0, 'AGF': 0, 'AGG': 0, 'B': 0, 'BA': 0, 'BAA': 0, 'BAB': 0, 'BAC': 0, 'BAD': 0, 'BAE': 0, 'BAF': 0, 'BAG': 0, 'BB': 0, 'BBA': 0, 'BBB': 0, 'BBC': 0, 'BBD': 0, 'BBE': 0, 'BBF': 0, 'BBG': 0, 'BC': 0, 'BCA': 0, 'BCB': 0, 'BCC': 0, 'BCD': 0, 'BCE': 0, 'BCF': 0, 'BCG': 0, 'BD': 0, 'BDA': 

TypeError: cannot unpack non-iterable int object

In [38]:
#!/usr/bin/python3 
from hyperparams import *
from rawdata_preprocessing import read_RPI_pairSeq, read_NPInter_pairSeq
from copy import deepcopy
import numpy as np

isPrint = True

# Reduced Protein letters(7 letters)
def get_reduced_protein_letter_dict():
    rpdict = {}
    reduced_letters = [["A","G","V"],
                       ["I","L","F","P"],
                       ["Y","M","T","S"],
                       ["H","N","Q","W"],
                       ["R","K"],
                       ["D","E"],
                       ["C"]]
    changed_letter = ["A","B","C","D","E","F","G"]
    for class_idx, class_letters in enumerate(reduced_letters):
        for letter in class_letters:
            rpdict[letter] = changed_letter[class_idx]
                
    #rpdict = {"A" : ["A","G","V"], "B" : ["I","L","F","P"], ... }
    return rpdict

# Improved CTF 
class improvedCTF:
    def __init__(self, letters, length):
        self.letters = letters
        self.length = length
        self.dict = {}
        self.generate_feature_dict()
        
    def generate_feature_dict(self):
        def generate(cur_key, depth):
            if depth == self.length:
                return
            for k in self.letters:
                next_key = cur_key + k
                self.dict[next_key] = 0
                generate(next_key, depth+1)
                
        generate(cur_key="",depth=0)
        
        if isPrint:
            print("iterate letters : {}".format(self.letters))
            print("number of keys  : {}".format(len(self.dict.keys())))
        
    
    def get_feature_dict(self):
        for k in self.dict.keys():
            self.dict[k] = 0
            
        return deepcopy(self.dict)

    
# CTF feature processing
def preprocess_feature(x, y, npz_path): # /data/npz/RPI369.npz 파일을 생성하는 함수.
# read_RPI_pairSeq(size) 의 return값 X, Y가 각각 x, y
# X : 2차원 배열 [[protein value1, rna value1], [protein value2, rna value2], ... ]
# Y : 1차원 배열. label의 배열 [1, 1, 1, ... , 0, 0, 0]
    
    def min_max_norm(a):
        a_min = np.min(a)
        a_max = np.max(a)
        return (a - a_min)/(a_max - a_min)
    
    rpdict = get_reduced_protein_letter_dict()
    feature_x = []
    r_mer = 4
    r_CTF = improvedCTF(letters=["A","C","G","U"],length=r_mer)
    #r_feature_dict = r_CTF.get_feature_dict()
    
    p_mer = 3
    p_CTF = improvedCTF(letters=["A","B","C","D","E","F","G"],length=p_mer)
    #p_feature_dict = p_CTF.get_feature_dict()
    
    x_protein = []
    x_rna = []
        
    for idx, (pseq, rseq) in enumerate(x): # pseq : protein value / rseq : RNA value
        
        r_feature_dict = r_CTF.get_feature_dict()
        p_feature_dict = p_CTF.get_feature_dict()
        #print("p_feature_dict : ", p_feature_dict)
        #print("r_feature_dict : ", r_feature_dict)
        rpseq = []
        #print("pseq : ", pseq)
        for p in pseq: # MQKGNFRNQRKTVKCFNCGKEGHIAKNCRAPRKKGCWKCGKEGHQMKDCTERQANX 의 각 알파벳을 p로 받으면서 순회한다.
            if p=="X": # MQKGNFRNQRKTVKCFNCGKEGHIAKNCRAPRKKGCWKCGKEGHQMKDCTERQANX 에서 X가 포함되어 있으면 ~?
                rpseq.append(p)
            else:
                rpseq.append(rpdict[p])
        #print("rpseq : ", rpseq)
        
                
        pseq = rpseq
        temp_pseq = ""
        for p in pseq:
            temp_pseq += p
        pseq = temp_pseq
        #print("temp_pseq : ", temp_pseq)
        
        for mer in range(1,p_mer+1):
            for i in range(0,len(pseq)-mer):
                pattern = pseq[i:i+mer]
                try:
                    p_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        
        for mer in range(1,r_mer+1):
            for i in range(0,len(rseq)-mer):
                pattern = rseq[i:i+mer]
                try:
                    r_feature_dict[pattern] += 1
                except:
                    continue
                #print(pattern)
        #print("p_feature_dict : ", p_feature_dict)
        #print("r_feature_dict : ", r_feature_dict)
        
        
        p_feature = np.array(list(p_feature_dict.values()))
        #if idx < 3 :
        #    print("p_feature_dict.key() : ", p_feature_dict.keys())
        if idx < 3 :
            print("r_feature_dict.key() : ", r_feature_dict.keys())
        
        print("p_feature before min_max_norm : ", p_feature)
        #print("len(p_feature) before min_max_norm : ", len(p_feature))
        p_feature = min_max_norm(p_feature)
        print("p_feature : ", p_feature)
        #print("len(p_feature) : ", len(p_feature))
        
        r_feature = np.array(list(r_feature_dict.values()))
        #print("r_feature before min_max_norm : ", r_feature)
        r_feature = min_max_norm(r_feature)
        #print("r_feature : ", r_feature)
        
        x_protein.append(p_feature)
        x_rna.append(r_feature)
        
        #if isPrint : 
            #print("CTF preprocessing ({} / {})".format(idx+1, len(x)))
            #print(r_feature)
        #return 0;   
                
    
    x_protein = np.array(x_protein)
    x_rna = np.array(x_rna)
    print("x_protein : ", x_protein)
    print("x_rna : ", x_rna)
    y = np.array(y)
    #for n, x_each_protein in enumerate(x_protein) :
        #print("(x_each_protein) : ", (x_each_protein))
    
    #np.savez(npz_path,XP=x_protein, XR=x_rna, Y=y)
    
    if isPrint :
        print("Protein feature : {}".format(x_protein.shape))
        print("RNA feature     : {}".format(x_rna.shape))
        print("Labels          : {}".format(y.shape))
        print("Saved path      : {}".format(npz_path))
    
        
    return x_protein, x_rna, y

def preprocess_and_savez_NPInter():
    X, Y = read_NPInter_pairSeq()
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["NPInter"])
    
def preprocess_and_savez_RPI(size):
    X, Y = read_RPI_pairSeq(size)
    XP, XR, Y = preprocess_feature(X, Y, NPZ_PATH["RPI"][size])
    

if __name__ == "__main__":
    print("Feature Preprocessing")
    #preprocess_and_savez_NPInter()
    #preprocess_and_savez_RPI(1807)
    #preprocess_and_savez_RPI(2241)
    preprocess_and_savez_RPI(369)
    #preprocess_and_savez_RPI(488)
    
    
    
    

Feature Preprocessing
iterate letters : ['A', 'C', 'G', 'U']
number of keys  : 340
iterate letters : ['A', 'B', 'C', 'D', 'E', 'F', 'G']
number of keys  : 399
r_feature_dict.key() :  dict_keys(['A', 'AA', 'AAA', 'AAAA', 'AAAC', 'AAAG', 'AAAU', 'AAC', 'AACA', 'AACC', 'AACG', 'AACU', 'AAG', 'AAGA', 'AAGC', 'AAGG', 'AAGU', 'AAU', 'AAUA', 'AAUC', 'AAUG', 'AAUU', 'AC', 'ACA', 'ACAA', 'ACAC', 'ACAG', 'ACAU', 'ACC', 'ACCA', 'ACCC', 'ACCG', 'ACCU', 'ACG', 'ACGA', 'ACGC', 'ACGG', 'ACGU', 'ACU', 'ACUA', 'ACUC', 'ACUG', 'ACUU', 'AG', 'AGA', 'AGAA', 'AGAC', 'AGAG', 'AGAU', 'AGC', 'AGCA', 'AGCC', 'AGCG', 'AGCU', 'AGG', 'AGGA', 'AGGC', 'AGGG', 'AGGU', 'AGU', 'AGUA', 'AGUC', 'AGUG', 'AGUU', 'AU', 'AUA', 'AUAA', 'AUAC', 'AUAG', 'AUAU', 'AUC', 'AUCA', 'AUCC', 'AUCG', 'AUCU', 'AUG', 'AUGA', 'AUGC', 'AUGG', 'AUGU', 'AUU', 'AUUA', 'AUUC', 'AUUG', 'AUUU', 'C', 'CA', 'CAA', 'CAAA', 'CAAC', 'CAAG', 'CAAU', 'CAC', 'CACA', 'CACC', 'CACG', 'CACU', 'CAG', 'CAGA', 'CAGC', 'CAGG', 'CAGU', 'CAU', 'CAUA', 'CAUC', 'C

p_feature before min_max_norm :  [67 15  1  3  3  3  1  4  0 14  1  5  2  3  1  2  0 12  1  3  2  2  3  1
  0  4  1  1  0  2  0  0  0 10  1  3  1  0  2  3  0 10  4  1  1  0  2  2
  0  2  2  0  0  0  0  0  0 73 13  3  2  3  0  2  1  2 19  5  4  2  2  3
  3  0  7  1  2  1  0  2  1  0  8  2  2  2  0  0  2  0 13  3  1  2  0  5
  2  0 12  2  3  2  2  1  2  0  1  0  0  1  0  0  0  0 41  4  2  0  0  0
  1  1  0 14  2  2  0  1  5  3  1  5  1  2  0  1  1  0  0  3  1  1  0  0
  0  1  0 10  1  5  1  1  1  1  0  4  0  1  1  1  0  1  0  0  0  0  0  0
  0  0  0 26  8  1  3  3  0  1  0  0  5  0  2  0  1  0  2  0  3  0  1  1
  0  0  0  0  2  1  0  0  0  0  1  0  1  0  1  0  0  0  0  0  7  3  0  1
  0  2  1  0  0  0  0  0  0  0  0  0 49 11  2  4  1  0  1  3  0 12  3  5
  1  1  2  0  0  5  0  2  0  0  3  0  0  4  1  0  1  0  0  2  0  9  5  1
  1  1  1  0  0  7  3  1  1  1  0  0  1  1  0  1  0  0  0  0  0 47 14  4
  2  2  1  4  1  0  8  2  1  2  0  2  1  0  7  1  4  1  0  0  1  0  4  1
  1  0  0  1  1  0

p_feature :  [0.79338843 0.18181818 0.00826446 0.07438017 0.02479339 0.01652893
 0.04132231 0.01652893 0.         0.19008264 0.04132231 0.04958678
 0.04132231 0.         0.02479339 0.03305785 0.         0.08264463
 0.03305785 0.02479339 0.         0.         0.         0.02479339
 0.         0.08264463 0.02479339 0.         0.02479339 0.
 0.02479339 0.00826446 0.         0.16528926 0.01652893 0.07438017
 0.02479339 0.         0.01652893 0.03305785 0.         0.08264463
 0.03305785 0.03305785 0.00826446 0.         0.         0.00826446
 0.         0.00826446 0.         0.00826446 0.         0.
 0.         0.         0.         1.         0.16528926 0.03305785
 0.03305785 0.01652893 0.03305785 0.03305785 0.01652893 0.
 0.27272727 0.04958678 0.05785124 0.07438017 0.02479339 0.03305785
 0.03305785 0.         0.19834711 0.03305785 0.0661157  0.02479339
 0.00826446 0.02479339 0.03305785 0.         0.09090909 0.02479339
 0.03305785 0.         0.00826446 0.00826446 0.01652893 0.
 0.12396694 0.

p_feature :  [0.83673469 0.16326531 0.04081633 0.00680272 0.01360544 0.02721088
 0.04081633 0.02721088 0.         0.19047619 0.03401361 0.04761905
 0.02040816 0.02040816 0.04081633 0.02721088 0.         0.10884354
 0.02721088 0.03401361 0.01360544 0.00680272 0.02721088 0.
 0.         0.06122449 0.02040816 0.02040816 0.00680272 0.
 0.00680272 0.00680272 0.         0.17687075 0.04081633 0.02040816
 0.01360544 0.00680272 0.04761905 0.04761905 0.         0.12244898
 0.00680272 0.06122449 0.01360544 0.00680272 0.00680272 0.02721088
 0.         0.00680272 0.         0.         0.00680272 0.
 0.         0.         0.         1.         0.2244898  0.04761905
 0.06802721 0.02040816 0.01360544 0.02721088 0.04081633 0.00680272
 0.20408163 0.06122449 0.02040816 0.05442177 0.         0.00680272
 0.05442177 0.00680272 0.14965986 0.01360544 0.04081633 0.02721088
 0.02040816 0.04081633 0.00680272 0.         0.08163265 0.01360544
 0.01360544 0.00680272 0.01360544 0.02040816 0.01360544 0.
 0.15646259 0.

p_feature :  [0.7    0.1875 0.075  0.0125 0.0125 0.     0.     0.075  0.0125 0.1125
 0.     0.     0.025  0.     0.0375 0.05   0.     0.1    0.025  0.025
 0.     0.     0.0125 0.025  0.0125 0.0625 0.     0.025  0.025  0.
 0.     0.0125 0.     0.1    0.     0.025  0.0375 0.     0.0125 0.025
 0.     0.125  0.05   0.0375 0.0125 0.     0.     0.025  0.     0.0125
 0.     0.0125 0.     0.     0.     0.     0.     1.     0.1625 0.05
 0.0375 0.     0.0125 0.0375 0.025  0.     0.2125 0.0375 0.05   0.05
 0.     0.05   0.025  0.     0.1125 0.0375 0.025  0.     0.0125 0.
 0.0375 0.     0.1375 0.025  0.05   0.025  0.0375 0.     0.     0.
 0.2125 0.0375 0.0125 0.0125 0.025  0.1125 0.0125 0.     0.1625 0.025
 0.05   0.0375 0.     0.025  0.025  0.     0.     0.     0.     0.
 0.     0.     0.     0.     0.55   0.0875 0.     0.025  0.0375 0.0125
 0.0125 0.     0.     0.1875 0.0375 0.05   0.     0.0375 0.0375 0.025
 0.     0.1    0.     0.025  0.025  0.     0.0125 0.0375 0.     0.025
 0.0125 0.     0. 

...

 0.         0.         0.        ]
p_feature before min_max_norm :  [15  2  0  1  0  0  1  0  0  5  0  1  0  0  1  3  0  2  1  0  1  0  0  0
  0  4  1  1  1  1  0  0  0  1  0  0  0  1  0  0  0  1  0  0  1  0  0  0
  0  0  0  0  0  0  0  0  0 20  2  0  1  1  0  0  0  0  4  0  0  2  0  1
  1  0  4  0  2  0  1  0  1  0  1  1  0  0  0  0  0  0  4  2  1  0  0  1
  0  0  5  1  2  0  0  1  1  0  0  0  0  0  0  0  0  0 11  3  1  0  1  1
  0  0  0  3  0  1  0  0  1  1  0  2  1  0  0  0  1  0  0  1  0  1  0  0
  0  0  0  1  1  0  0  0  0  0  0  1  0  0  0  0  1  0  0  0  0  0  0  0
  0  0  0 10  3  1  1  0  1  0  0  0  3  2  1  0  0  0  0  0  1  0  1  0
  0  0  0  0  3  0  1  0  2  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0 10  3  0  1  0  2  0  0  0  3  0  0
  2  1  0  0  0  0  0  0  0  0  0  0  0  1  1  0  0  0  0  0  0  2  0  2
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  8  1  0
  1  0  0  0  0  0  2  0  1  0  0  1  0  0  1  1  0  0  

 0.   0.   0.   0.   0.   0.   0.  ]
p_feature before min_max_norm :  [31  4  0  0  1  2  1  0  0  8  0  2  1  1  0  4  0  4  0  2  0  1  1  0
  0  3  0  1  1  1  0  0  0  6  1  2  0  0  1  2  0  5  1  3  0  0  1  0
  0  0  0  0  0  0  0  0  0 51 10  1  1  2  1  1  3  0 11  3  3  1  0  2
  2  0  7  2  0  1  1  1  2  0  2  1  0  0  0  1  0  0  8  2  0  2  1  2
  1  0 11  2  5  0  4  0  0  0  2  0  1  0  0  1  0  0 20  3  0  1  0  0
  1  1  0  7  1  1  1  0  2  1  1  2  0  1  0  1  0  0  0  3  1  0  0  1
  1  0  0  3  1  2  0  0  0  0  0  2  0  1  0  1  0  0  0  0  0  0  0  0
  0  0  0 19  4  2  1  0  0  1  0  0  4  3  0  0  0  0  1  0  3  0  1  1
  0  1  0  0  3  0  0  1  1  1  0  0  3  1  1  0  0  1  0  0  2  1  1  0
  0  0  0  0  0  0  0  0  0  0  0  0 28  6  1  2  1  0  2  0  0  8  1  1
  2  0  2  1  1  3  0  3  0  0  0  0  0  3  0  1  1  0  0  1  0  4  1  2
  0  1  0  0  0  4  0  2  0  0  2  0  0  0  0  0  0  0  0  0  0 24  4  0
  3  0  0  0  1  0 12  2  3  2  1  2  2  0  0  0  0  0

 0.         0.         0.        ]
p_feature before min_max_norm :  [218  53  12  16   6   1   6  11   1  80  23  21   8   6  11  11   0  24
   7   8   2   2   3   2   0  11   1   4   0   0   5   1   0  19   6   2
   2   0   4   5   0  29  15   2   2   2   3   5   0   2   0   1   0   0
   1   0   0 240  62  14  25   8   5   5   4   1  67  20  24   3   6   5
   9   0  18   3   6   1   4   2   2   0  15   4   6   1   1   1   2   0
  31   9   8   3   1   4   6   0  47  16  12   5   1   7   6   0   0   0
   0   0   0   0   0   0  71  15   3   5   2   1   2   2   0  25   4   7
   2   2   4   6   0   6   0   2   3   0   1   0   0   9   2   3   1   0
   3   0   0   7   3   2   0   1   1   0   0   8   4   2   1   0   1   0
   0   0   0   0   0   0   0   0   0  44  10   2   6   0   0   2   0   0
  17   4   4   2   0   3   4   0   2   1   0   0   1   0   0   0   1   1
   0   0   0   0   0   0  11   4   5   1   0   1   0   0   3   1   2   0
   0   0   0   0   0   0   0   0   0   0   0   0  93  32

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




p_feature before min_max_norm :  [37 11  4  1  2  2  0  2  0  6  2  1  1  0  1  0  0  8  2  0  0  4  1  0
  1  5  1  1  1  1  1  0  0  2  1  0  0  1  0  0  0  5  2  1  0  2  0  0
  0  0  0  0  0  0  0  0  0 25  7  2  1  1  1  1  1  0  8  3  3  1  0  1
  0  0  5  1  1  1  2  0  0  0  1  0  0  1  0  0  0  0  3  2  0  0  0  0
  1  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0 27  7  2  2  0  1
  1  1  0  3  0  1  0  1  1  0  0  4  1  2  0  1  0  0  0  8  2  3  3  0
  0  0  0  2  1  0  1  0  0  0  0  2  0  1  0  0  0  0  1  1  0  0  1  0
  0  0  0 18  4  2  1  1  0  0  0  0  5  2  1  2  0  0  0  0  6  2  0  1
  0  1  2  0  1  0  0  0  0  1  0  0  2  0  0  1  0  1  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0 10  4  1  0  2  0  0  1  0  0  0  0
  0  0  0  0  0  3  0  0  2  1  0  0  0  1  0  0  1  0  0  0  0  1  0  0
  1  0  0  0  0  1  1  0  0  0  0  0  0  0  0  0  0  0  0  0  0  9  3  0
  1  1  1  0  0  0  3  0  2  1  0  0  0  0  0  0  0  0  0  0  0  0  2  1
  1  0  0  0  0  

In [12]:
mydata = np.load('./npz/RPI369.npz')
XP = mydata['XP']
XP

array([[0.51851852, 0.03703704, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.74916388, 0.09364548, 0.01672241, ..., 0.        , 0.        ,
        0.        ],
       [0.78199052, 0.15876777, 0.02132701, ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.42424242, 0.04545455, 0.01515152, ..., 0.        , 0.        ,
        0.        ],
       [0.57142857, 0.06122449, 0.01020408, ..., 0.        , 0.        ,
        0.        ],
       [1.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [26]:
import pandas as pd
feature_names = ['A', 'AA', 'AAA', 'AAB', 'AAC', 'AAD', 'AAE', 'AAF', 'AAG', 'AB', 'ABA', 'ABB', 'ABC', 'ABD', 'ABE', 'ABF', 'ABG', 'AC', 'ACA', 'ACB', 'ACC', 'ACD', 'ACE', 'ACF', 'ACG', 'AD', 'ADA', 'ADB', 'ADC', 'ADD', 'ADE', 'ADF', 'ADG', 'AE', 'AEA', 'AEB', 'AEC', 'AED', 'AEE', 'AEF', 'AEG', 'AF', 'AFA', 'AFB', 'AFC', 'AFD', 'AFE', 'AFF', 'AFG', 'AG', 'AGA', 'AGB', 'AGC', 'AGD', 'AGE', 'AGF', 'AGG', 'B', 'BA', 'BAA', 'BAB', 'BAC', 'BAD', 'BAE', 'BAF', 'BAG', 'BB', 'BBA', 'BBB', 'BBC', 'BBD', 'BBE', 'BBF', 'BBG', 'BC', 'BCA', 'BCB', 'BCC', 'BCD', 'BCE', 'BCF', 'BCG', 'BD', 'BDA', 'BDB', 'BDC', 'BDD', 'BDE', 'BDF', 'BDG', 'BE', 'BEA', 'BEB', 'BEC', 'BED', 'BEE', 'BEF', 'BEG', 'BF', 'BFA', 'BFB', 'BFC', 'BFD', 'BFE', 'BFF', 'BFG', 'BG', 'BGA', 'BGB', 'BGC', 'BGD', 'BGE', 'BGF', 'BGG', 'C', 'CA', 'CAA', 'CAB', 'CAC', 'CAD', 'CAE', 'CAF', 'CAG', 'CB', 'CBA', 'CBB', 'CBC', 'CBD', 'CBE', 'CBF', 'CBG', 'CC', 'CCA', 'CCB', 'CCC', 'CCD', 'CCE', 'CCF', 'CCG', 'CD', 'CDA', 'CDB', 'CDC', 'CDD', 'CDE', 'CDF', 'CDG', 'CE', 'CEA', 'CEB', 'CEC', 'CED', 'CEE', 'CEF', 'CEG', 'CF', 'CFA', 'CFB', 'CFC', 'CFD', 'CFE', 'CFF', 'CFG', 'CG', 'CGA', 'CGB', 'CGC', 'CGD', 'CGE', 'CGF', 'CGG', 'D', 'DA', 'DAA', 'DAB', 'DAC', 'DAD', 'DAE', 'DAF', 'DAG', 'DB', 'DBA', 'DBB', 'DBC', 'DBD', 'DBE', 'DBF', 'DBG', 'DC', 'DCA', 'DCB', 'DCC', 'DCD', 'DCE', 'DCF', 'DCG', 'DD', 'DDA', 'DDB', 'DDC', 'DDD', 'DDE', 'DDF', 'DDG', 'DE', 'DEA', 'DEB', 'DEC', 'DED', 'DEE', 'DEF', 'DEG', 'DF', 'DFA', 'DFB', 'DFC', 'DFD', 'DFE', 'DFF', 'DFG', 'DG', 'DGA', 'DGB', 'DGC', 'DGD', 'DGE', 'DGF', 'DGG', 'E', 'EA', 'EAA', 'EAB', 'EAC', 'EAD', 'EAE', 'EAF', 'EAG', 'EB', 'EBA', 'EBB', 'EBC', 'EBD', 'EBE', 'EBF', 'EBG', 'EC', 'ECA', 'ECB', 'ECC', 'ECD', 'ECE', 'ECF', 'ECG', 'ED', 'EDA', 'EDB', 'EDC', 'EDD', 'EDE', 'EDF', 'EDG', 'EE', 'EEA', 'EEB', 'EEC', 'EED', 'EEE', 'EEF', 'EEG', 'EF', 'EFA', 'EFB', 'EFC', 'EFD', 'EFE', 'EFF', 'EFG', 'EG', 'EGA', 'EGB', 'EGC', 'EGD', 'EGE', 'EGF', 'EGG', 'F', 'FA', 'FAA', 'FAB', 'FAC', 'FAD', 'FAE', 'FAF', 'FAG', 'FB', 'FBA', 'FBB', 'FBC', 'FBD', 'FBE', 'FBF', 'FBG', 'FC', 'FCA', 'FCB', 'FCC', 'FCD', 'FCE', 'FCF', 'FCG', 'FD', 'FDA', 'FDB', 'FDC', 'FDD', 'FDE', 'FDF', 'FDG', 'FE', 'FEA', 'FEB', 'FEC', 'FED', 'FEE', 'FEF', 'FEG', 'FF', 'FFA', 'FFB', 'FFC', 'FFD', 'FFE', 'FFF', 'FFG', 'FG', 'FGA', 'FGB', 'FGC', 'FGD', 'FGE', 'FGF', 'FGG', 'G', 'GA', 'GAA', 'GAB', 'GAC', 'GAD', 'GAE', 'GAF', 'GAG', 'GB', 'GBA', 'GBB', 'GBC', 'GBD', 'GBE', 'GBF', 'GBG', 'GC', 'GCA', 'GCB', 'GCC', 'GCD', 'GCE', 'GCF', 'GCG', 'GD', 'GDA', 'GDB', 'GDC', 'GDD', 'GDE', 'GDF', 'GDG', 'GE', 'GEA', 'GEB', 'GEC', 'GED', 'GEE', 'GEF', 'GEG', 'GF', 'GFA', 'GFB', 'GFC', 'GFD', 'GFE', 'GFF', 'GFG', 'GG', 'GGA', 'GGB', 'GGC', 'GGD', 'GGE', 'GGF', 'GGG']
print(len(feature_names))
Y = mydata['Y']
XP_pd = pd.DataFrame(data= np.c_[XP, Y], columns= feature_names + ['target'])
#XP_pd = pd.DataFrame(data= XP, columns= feature_names)

399


In [28]:
from sklearn.model_selection import KFold

In [30]:
cv=KFold(n_splits=3,random_state=None,shuffle=False)

In [36]:
for t,v in cv.split(XP_pd):
    train_XP_cv=XP_pd.iloc[t]       # 훈련용
    val_XP_cv=XP_pd.iloc[v]         # 검증용 분리.
    
    print(val_XP_cv.head(10))


          A        AA       AAA       AAB       AAC       AAD       AAE  \
0  0.518519  0.037037  0.000000  0.037037  0.000000  0.000000  0.000000   
1  0.749164  0.093645  0.016722  0.026756  0.020067  0.016722  0.010033   
2  0.781991  0.158768  0.021327  0.040284  0.037915  0.018957  0.023697   
3  0.626087  0.121739  0.034783  0.017391  0.008696  0.026087  0.017391   
4  0.750000  0.031250  0.000000  0.000000  0.000000  0.031250  0.000000   
5  1.000000  0.333333  0.041667  0.083333  0.041667  0.041667  0.125000   
6  1.000000  0.294737  0.105263  0.063158  0.084211  0.042105  0.000000   
7  1.000000  0.333333  0.083333  0.083333  0.083333  0.083333  0.000000   
8  0.750000  0.100000  0.000000  0.050000  0.000000  0.000000  0.050000   
9  1.000000  0.206897  0.068966  0.034483  0.000000  0.000000  0.068966   

        AAF      AAG        AB  ...      GFG       GG  GGA      GGB  GGC  GGD  \
0  0.000000  0.00000  0.222222  ...  0.00000  0.00000  0.0  0.00000  0.0  0.0   
1  0.003344 

In [39]:
XR = mydata['XR']
r_feature_names = ['A', 'AA', 'AAA', 'AAAA', 'AAAC', 'AAAG', 'AAAU', 'AAC', 'AACA', 'AACC', 'AACG', 'AACU', 'AAG', 'AAGA', 'AAGC', 'AAGG', 'AAGU', 'AAU', 'AAUA', 'AAUC', 'AAUG', 'AAUU', 'AC', 'ACA', 'ACAA', 'ACAC', 'ACAG', 'ACAU', 'ACC', 'ACCA', 'ACCC', 'ACCG', 'ACCU', 'ACG', 'ACGA', 'ACGC', 'ACGG', 'ACGU', 'ACU', 'ACUA', 'ACUC', 'ACUG', 'ACUU', 'AG', 'AGA', 'AGAA', 'AGAC', 'AGAG', 'AGAU', 'AGC', 'AGCA', 'AGCC', 'AGCG', 'AGCU', 'AGG', 'AGGA', 'AGGC', 'AGGG', 'AGGU', 'AGU', 'AGUA', 'AGUC', 'AGUG', 'AGUU', 'AU', 'AUA', 'AUAA', 'AUAC', 'AUAG', 'AUAU', 'AUC', 'AUCA', 'AUCC', 'AUCG', 'AUCU', 'AUG', 'AUGA', 'AUGC', 'AUGG', 'AUGU', 'AUU', 'AUUA', 'AUUC', 'AUUG', 'AUUU', 'C', 'CA', 'CAA', 'CAAA', 'CAAC', 'CAAG', 'CAAU', 'CAC', 'CACA', 'CACC', 'CACG', 'CACU', 'CAG', 'CAGA', 'CAGC', 'CAGG', 'CAGU', 'CAU', 'CAUA', 'CAUC', 'CAUG', 'CAUU', 'CC', 'CCA', 'CCAA', 'CCAC', 'CCAG', 'CCAU', 'CCC', 'CCCA', 'CCCC', 'CCCG', 'CCCU', 'CCG', 'CCGA', 'CCGC', 'CCGG', 'CCGU', 'CCU', 'CCUA', 'CCUC', 'CCUG', 'CCUU', 'CG', 'CGA', 'CGAA', 'CGAC', 'CGAG', 'CGAU', 'CGC', 'CGCA', 'CGCC', 'CGCG', 'CGCU', 'CGG', 'CGGA', 'CGGC', 'CGGG', 'CGGU', 'CGU', 'CGUA', 'CGUC', 'CGUG', 'CGUU', 'CU', 'CUA', 'CUAA', 'CUAC', 'CUAG', 'CUAU', 'CUC', 'CUCA', 'CUCC', 'CUCG', 'CUCU', 'CUG', 'CUGA', 'CUGC', 'CUGG', 'CUGU', 'CUU', 'CUUA', 'CUUC', 'CUUG', 'CUUU', 'G', 'GA', 'GAA', 'GAAA', 'GAAC', 'GAAG', 'GAAU', 'GAC', 'GACA', 'GACC', 'GACG', 'GACU', 'GAG', 'GAGA', 'GAGC', 'GAGG', 'GAGU', 'GAU', 'GAUA', 'GAUC', 'GAUG', 'GAUU', 'GC', 'GCA', 'GCAA', 'GCAC', 'GCAG', 'GCAU', 'GCC', 'GCCA', 'GCCC', 'GCCG', 'GCCU', 'GCG', 'GCGA', 'GCGC', 'GCGG', 'GCGU', 'GCU', 'GCUA', 'GCUC', 'GCUG', 'GCUU', 'GG', 'GGA', 'GGAA', 'GGAC', 'GGAG', 'GGAU', 'GGC', 'GGCA', 'GGCC', 'GGCG', 'GGCU', 'GGG', 'GGGA', 'GGGC', 'GGGG', 'GGGU', 'GGU', 'GGUA', 'GGUC', 'GGUG', 'GGUU', 'GU', 'GUA', 'GUAA', 'GUAC', 'GUAG', 'GUAU', 'GUC', 'GUCA', 'GUCC', 'GUCG', 'GUCU', 'GUG', 'GUGA', 'GUGC', 'GUGG', 'GUGU', 'GUU', 'GUUA', 'GUUC', 'GUUG', 'GUUU', 'U', 'UA', 'UAA', 'UAAA', 'UAAC', 'UAAG', 'UAAU', 'UAC', 'UACA', 'UACC', 'UACG', 'UACU', 'UAG', 'UAGA', 'UAGC', 'UAGG', 'UAGU', 'UAU', 'UAUA', 'UAUC', 'UAUG', 'UAUU', 'UC', 'UCA', 'UCAA', 'UCAC', 'UCAG', 'UCAU', 'UCC', 'UCCA', 'UCCC', 'UCCG', 'UCCU', 'UCG', 'UCGA', 'UCGC', 'UCGG', 'UCGU', 'UCU', 'UCUA', 'UCUC', 'UCUG', 'UCUU', 'UG', 'UGA', 'UGAA', 'UGAC', 'UGAG', 'UGAU', 'UGC', 'UGCA', 'UGCC', 'UGCG', 'UGCU', 'UGG', 'UGGA', 'UGGC', 'UGGG', 'UGGU', 'UGU', 'UGUA', 'UGUC', 'UGUG', 'UGUU', 'UU', 'UUA', 'UUAA', 'UUAC', 'UUAG', 'UUAU', 'UUC', 'UUCA', 'UUCC', 'UUCG', 'UUCU', 'UUG', 'UUGA', 'UUGC', 'UUGG', 'UUGU', 'UUU', 'UUUA', 'UUUC', 'UUUG', 'UUUU']
XR_pd = pd.DataFrame(data= np.c_[XR, Y], columns= feature_names + ['target'])

for tr,vr in cv.split(XR_pd):
    train_XR_cv=XP_pd.iloc[tr]       # 훈련용
    val_XR_cv=XP_pd.iloc[vr]         # 검증용 분리.
    
    print(val_XR_cv.head(10))

ValueError: Shape of passed values is (738, 341), indices imply (738, 400)

In [40]:
XR = mydata['XR']
r_feature_names = ['A', 'AA', 'AAA', 'AAAA', 'AAAC', 'AAAG', 'AAAU', 'AAC', 'AACA', 'AACC', 'AACG', 'AACU', 'AAG', 'AAGA', 'AAGC', 'AAGG', 'AAGU', 'AAU', 'AAUA', 'AAUC', 'AAUG', 'AAUU', 'AC', 'ACA', 'ACAA', 'ACAC', 'ACAG', 'ACAU', 'ACC', 'ACCA', 'ACCC', 'ACCG', 'ACCU', 'ACG', 'ACGA', 'ACGC', 'ACGG', 'ACGU', 'ACU', 'ACUA', 'ACUC', 'ACUG', 'ACUU', 'AG', 'AGA', 'AGAA', 'AGAC', 'AGAG', 'AGAU', 'AGC', 'AGCA', 'AGCC', 'AGCG', 'AGCU', 'AGG', 'AGGA', 'AGGC', 'AGGG', 'AGGU', 'AGU', 'AGUA', 'AGUC', 'AGUG', 'AGUU', 'AU', 'AUA', 'AUAA', 'AUAC', 'AUAG', 'AUAU', 'AUC', 'AUCA', 'AUCC', 'AUCG', 'AUCU', 'AUG', 'AUGA', 'AUGC', 'AUGG', 'AUGU', 'AUU', 'AUUA', 'AUUC', 'AUUG', 'AUUU', 'C', 'CA', 'CAA', 'CAAA', 'CAAC', 'CAAG', 'CAAU', 'CAC', 'CACA', 'CACC', 'CACG', 'CACU', 'CAG', 'CAGA', 'CAGC', 'CAGG', 'CAGU', 'CAU', 'CAUA', 'CAUC', 'CAUG', 'CAUU', 'CC', 'CCA', 'CCAA', 'CCAC', 'CCAG', 'CCAU', 'CCC', 'CCCA', 'CCCC', 'CCCG', 'CCCU', 'CCG', 'CCGA', 'CCGC', 'CCGG', 'CCGU', 'CCU', 'CCUA', 'CCUC', 'CCUG', 'CCUU', 'CG', 'CGA', 'CGAA', 'CGAC', 'CGAG', 'CGAU', 'CGC', 'CGCA', 'CGCC', 'CGCG', 'CGCU', 'CGG', 'CGGA', 'CGGC', 'CGGG', 'CGGU', 'CGU', 'CGUA', 'CGUC', 'CGUG', 'CGUU', 'CU', 'CUA', 'CUAA', 'CUAC', 'CUAG', 'CUAU', 'CUC', 'CUCA', 'CUCC', 'CUCG', 'CUCU', 'CUG', 'CUGA', 'CUGC', 'CUGG', 'CUGU', 'CUU', 'CUUA', 'CUUC', 'CUUG', 'CUUU', 'G', 'GA', 'GAA', 'GAAA', 'GAAC', 'GAAG', 'GAAU', 'GAC', 'GACA', 'GACC', 'GACG', 'GACU', 'GAG', 'GAGA', 'GAGC', 'GAGG', 'GAGU', 'GAU', 'GAUA', 'GAUC', 'GAUG', 'GAUU', 'GC', 'GCA', 'GCAA', 'GCAC', 'GCAG', 'GCAU', 'GCC', 'GCCA', 'GCCC', 'GCCG', 'GCCU', 'GCG', 'GCGA', 'GCGC', 'GCGG', 'GCGU', 'GCU', 'GCUA', 'GCUC', 'GCUG', 'GCUU', 'GG', 'GGA', 'GGAA', 'GGAC', 'GGAG', 'GGAU', 'GGC', 'GGCA', 'GGCC', 'GGCG', 'GGCU', 'GGG', 'GGGA', 'GGGC', 'GGGG', 'GGGU', 'GGU', 'GGUA', 'GGUC', 'GGUG', 'GGUU', 'GU', 'GUA', 'GUAA', 'GUAC', 'GUAG', 'GUAU', 'GUC', 'GUCA', 'GUCC', 'GUCG', 'GUCU', 'GUG', 'GUGA', 'GUGC', 'GUGG', 'GUGU', 'GUU', 'GUUA', 'GUUC', 'GUUG', 'GUUU', 'U', 'UA', 'UAA', 'UAAA', 'UAAC', 'UAAG', 'UAAU', 'UAC', 'UACA', 'UACC', 'UACG', 'UACU', 'UAG', 'UAGA', 'UAGC', 'UAGG', 'UAGU', 'UAU', 'UAUA', 'UAUC', 'UAUG', 'UAUU', 'UC', 'UCA', 'UCAA', 'UCAC', 'UCAG', 'UCAU', 'UCC', 'UCCA', 'UCCC', 'UCCG', 'UCCU', 'UCG', 'UCGA', 'UCGC', 'UCGG', 'UCGU', 'UCU', 'UCUA', 'UCUC', 'UCUG', 'UCUU', 'UG', 'UGA', 'UGAA', 'UGAC', 'UGAG', 'UGAU', 'UGC', 'UGCA', 'UGCC', 'UGCG', 'UGCU', 'UGG', 'UGGA', 'UGGC', 'UGGG', 'UGGU', 'UGU', 'UGUA', 'UGUC', 'UGUG', 'UGUU', 'UU', 'UUA', 'UUAA', 'UUAC', 'UUAG', 'UUAU', 'UUC', 'UUCA', 'UUCC', 'UUCG', 'UUCU', 'UUG', 'UUGA', 'UUGC', 'UUGG', 'UUGU', 'UUU', 'UUUA', 'UUUC', 'UUUG', 'UUUU']

In [41]:
print(len(r_feature_names))

340


In [66]:

XR = mydata['XR']
r_feature_names = ['A', 'AA', 'AAA', 'AAAA', 'AAAC', 'AAAG', 'AAAU', 'AAC', 'AACA', 'AACC', 'AACG', 'AACU', 'AAG', 'AAGA', 'AAGC', 'AAGG', 'AAGU', 'AAU', 'AAUA', 'AAUC', 'AAUG', 'AAUU', 'AC', 'ACA', 'ACAA', 'ACAC', 'ACAG', 'ACAU', 'ACC', 'ACCA', 'ACCC', 'ACCG', 'ACCU', 'ACG', 'ACGA', 'ACGC', 'ACGG', 'ACGU', 'ACU', 'ACUA', 'ACUC', 'ACUG', 'ACUU', 'AG', 'AGA', 'AGAA', 'AGAC', 'AGAG', 'AGAU', 'AGC', 'AGCA', 'AGCC', 'AGCG', 'AGCU', 'AGG', 'AGGA', 'AGGC', 'AGGG', 'AGGU', 'AGU', 'AGUA', 'AGUC', 'AGUG', 'AGUU', 'AU', 'AUA', 'AUAA', 'AUAC', 'AUAG', 'AUAU', 'AUC', 'AUCA', 'AUCC', 'AUCG', 'AUCU', 'AUG', 'AUGA', 'AUGC', 'AUGG', 'AUGU', 'AUU', 'AUUA', 'AUUC', 'AUUG', 'AUUU', 'C', 'CA', 'CAA', 'CAAA', 'CAAC', 'CAAG', 'CAAU', 'CAC', 'CACA', 'CACC', 'CACG', 'CACU', 'CAG', 'CAGA', 'CAGC', 'CAGG', 'CAGU', 'CAU', 'CAUA', 'CAUC', 'CAUG', 'CAUU', 'CC', 'CCA', 'CCAA', 'CCAC', 'CCAG', 'CCAU', 'CCC', 'CCCA', 'CCCC', 'CCCG', 'CCCU', 'CCG', 'CCGA', 'CCGC', 'CCGG', 'CCGU', 'CCU', 'CCUA', 'CCUC', 'CCUG', 'CCUU', 'CG', 'CGA', 'CGAA', 'CGAC', 'CGAG', 'CGAU', 'CGC', 'CGCA', 'CGCC', 'CGCG', 'CGCU', 'CGG', 'CGGA', 'CGGC', 'CGGG', 'CGGU', 'CGU', 'CGUA', 'CGUC', 'CGUG', 'CGUU', 'CU', 'CUA', 'CUAA', 'CUAC', 'CUAG', 'CUAU', 'CUC', 'CUCA', 'CUCC', 'CUCG', 'CUCU', 'CUG', 'CUGA', 'CUGC', 'CUGG', 'CUGU', 'CUU', 'CUUA', 'CUUC', 'CUUG', 'CUUU', 'G', 'GA', 'GAA', 'GAAA', 'GAAC', 'GAAG', 'GAAU', 'GAC', 'GACA', 'GACC', 'GACG', 'GACU', 'GAG', 'GAGA', 'GAGC', 'GAGG', 'GAGU', 'GAU', 'GAUA', 'GAUC', 'GAUG', 'GAUU', 'GC', 'GCA', 'GCAA', 'GCAC', 'GCAG', 'GCAU', 'GCC', 'GCCA', 'GCCC', 'GCCG', 'GCCU', 'GCG', 'GCGA', 'GCGC', 'GCGG', 'GCGU', 'GCU', 'GCUA', 'GCUC', 'GCUG', 'GCUU', 'GG', 'GGA', 'GGAA', 'GGAC', 'GGAG', 'GGAU', 'GGC', 'GGCA', 'GGCC', 'GGCG', 'GGCU', 'GGG', 'GGGA', 'GGGC', 'GGGG', 'GGGU', 'GGU', 'GGUA', 'GGUC', 'GGUG', 'GGUU', 'GU', 'GUA', 'GUAA', 'GUAC', 'GUAG', 'GUAU', 'GUC', 'GUCA', 'GUCC', 'GUCG', 'GUCU', 'GUG', 'GUGA', 'GUGC', 'GUGG', 'GUGU', 'GUU', 'GUUA', 'GUUC', 'GUUG', 'GUUU', 'U', 'UA', 'UAA', 'UAAA', 'UAAC', 'UAAG', 'UAAU', 'UAC', 'UACA', 'UACC', 'UACG', 'UACU', 'UAG', 'UAGA', 'UAGC', 'UAGG', 'UAGU', 'UAU', 'UAUA', 'UAUC', 'UAUG', 'UAUU', 'UC', 'UCA', 'UCAA', 'UCAC', 'UCAG', 'UCAU', 'UCC', 'UCCA', 'UCCC', 'UCCG', 'UCCU', 'UCG', 'UCGA', 'UCGC', 'UCGG', 'UCGU', 'UCU', 'UCUA', 'UCUC', 'UCUG', 'UCUU', 'UG', 'UGA', 'UGAA', 'UGAC', 'UGAG', 'UGAU', 'UGC', 'UGCA', 'UGCC', 'UGCG', 'UGCU', 'UGG', 'UGGA', 'UGGC', 'UGGG', 'UGGU', 'UGU', 'UGUA', 'UGUC', 'UGUG', 'UGUU', 'UU', 'UUA', 'UUAA', 'UUAC', 'UUAG', 'UUAU', 'UUC', 'UUCA', 'UUCC', 'UUCG', 'UUCU', 'UUG', 'UUGA', 'UUGC', 'UUGG', 'UUGU', 'UUU', 'UUUA', 'UUUC', 'UUUG', 'UUUU']
XR_pd = pd.DataFrame(data= np.c_[XR, Y], columns= r_feature_names + ['target'])

for tr,vr in cv.split(XR_pd):
    train_XR_cv=XR_pd.iloc[tr]       # 훈련용
    val_XR_cv=XR_pd.iloc[vr]         # 검증용 분리.
    
    print(val_XR_cv.head(10))




          A        AA       AAA      AAAA   AAAC  AAAG      AAAU       AAC  \
0  0.400000  0.080000  0.000000  0.000000  0.000   0.0  0.000000  0.040000   
1  0.571429  0.142857  0.000000  0.000000  0.000   0.0  0.000000  0.000000   
2  0.571429  0.142857  0.000000  0.000000  0.000   0.0  0.000000  0.000000   
3  0.583333  0.125000  0.083333  0.041667  0.000   0.0  0.041667  0.000000   
4  0.777778  0.111111  0.000000  0.000000  0.000   0.0  0.000000  0.111111   
5  0.714286  0.000000  0.000000  0.000000  0.000   0.0  0.000000  0.000000   
6  0.200000  0.150000  0.100000  0.050000  0.000   0.0  0.050000  0.000000   
7  0.200000  0.150000  0.100000  0.050000  0.000   0.0  0.050000  0.000000   
8  0.700000  0.150000  0.050000  0.000000  0.025   0.0  0.025000  0.025000   
9  0.700000  0.150000  0.050000  0.000000  0.025   0.0  0.025000  0.025000   

   AACA      AACC  ...  UUGA  UUGC      UUGG   UUGU    UUU  UUUA   UUUC  \
0  0.04  0.000000  ...   0.0  0.04  0.000000  0.000  0.000  0.00  

In [71]:
print(XP_pd.info())
print(XR_pd.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 738 entries, 0 to 737
Columns: 400 entries, A to target
dtypes: float64(400)
memory usage: 2.3 MB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 738 entries, 0 to 737
Columns: 341 entries, A to target
dtypes: float64(341)
memory usage: 1.9 MB
None


In [73]:
combined_pd = pd.DataFrame(data= np.c_[np.c_[XP, XR], Y], columns= feature_names + r_feature_names + ['target'])
combined_pd.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 738 entries, 0 to 737
Columns: 740 entries, A to target
dtypes: float64(740)
memory usage: 4.2 MB


In [74]:
combined_pd.head(10)

A        AA       AAA       AAB       AAC       AAD       AAE  \
0  0.518519  0.037037  0.000000  0.037037  0.000000  0.000000  0.000000   
1  0.749164  0.093645  0.016722  0.026756  0.020067  0.016722  0.010033   
2  0.781991  0.158768  0.021327  0.040284  0.037915  0.018957  0.023697   
3  0.626087  0.121739  0.034783  0.017391  0.008696  0.026087  0.017391   
4  0.750000  0.031250  0.000000  0.000000  0.000000  0.031250  0.000000   
5  1.000000  0.333333  0.041667  0.083333  0.041667  0.041667  0.125000   
6  1.000000  0.294737  0.105263  0.063158  0.084211  0.042105  0.000000   
7  1.000000  0.333333  0.083333  0.083333  0.083333  0.083333  0.000000   
8  0.750000  0.100000  0.000000  0.050000  0.000000  0.000000  0.050000   
9  1.000000  0.206897  0.068966  0.034483  0.000000  0.000000  0.068966   

        AAF      AAG        AB  ...  UUGA  UUGC      UUGG   UUGU    UUU  UUUA  \
0  0.000000  0.00000  0.222222  ...   0.0  0.04  0.000000  0.000  0.000  0.00   
1  0.003344  0.00000  0.204013  ...   0.0  0.00  0.000000  0.000  0.000  0.00   
2  0.014218  0.00237  0.189573  ...   0.0  0.00  0.000000  0.000  0.000  0.00   
3  0.017391  0.00000  0.165217  ...   0.0  0.00  0.041667  0.000  0.000  0.00   
4  0.000000  0.00000  0.156250  ...   0.0  0.00  0.000000  0.000  0.000  0.00   
5  0.000000  0.00000  0.083333  ...   0.0  0.00  0.000000  0.000  0.000  0.00   
6  0.000000  0.00000  0.336842  ...   0.0  0.00  0.000000  0.000  0.800  0.05   
7  0.000000  0.00000  0.333333  ...   0.0  0.00  0.000000  0.000  0.800  0.05   
8  0.000000  0.00000  0.250000  ...   0.0  0.00  0.000000  0.025  0.125  0.00   
9  0.034483  0.00000  0.034483  ...   0.0  0.00  0.000000  0.025  0.125  0.00   

    UUUC   UUUG   UUUU  target  
0  0.000  0.000  0.000     1.0  
1  0.000  0.000  0.000     1.0  
2  0.000  0.000  0.000     1.0  
3  0.000  0.000  0.000     1.0  
4  0.000  0.000  0.000     1.0  
5  0.000  0.000  0.000     1.0  
6  0.000  0.000  0.700     1.0  
7  0.000  0.000  0.700     1.0  
8  0.075  0.025  0.025     1.0  
9  0.075  0.025  0.025     1.0  

[10 rows x 740 columns]

In [95]:
from sklearn.model_selection import KFold
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import RandomForestClassifier


features = list(combined_pd.columns[:-1])
X = combined_pd[features]
y = combined_pd['target']


rf = RandomForestClassifier(random_state=1)
score_list = cross_val_score(rf, X, y, cv=5)
result = list(map(lambda x: '{score:.2f}'.format(score=x), score_list))
print(result)
'''
cv=KFold(n_splits=3,random_state=5,shuffle=True)

train_combined_arr = []
val_combined_arr = []

for t,v in cv.split(combined_pd):
    train_combined_cv=combined_pd.iloc[t]       # 훈련용
    val_combined_cv=combined_pd.iloc[v]         # 검증용 분리.
    
    train_combined_arr.append(train_combined_cv)
    val_combined_arr.append(val_combined_cv)
    
    features = list(train_combined_cv.columns[:-1])
    X = train_combined_cv[features]
    y = train_combined_cv['target']
    tree_clf.fit(X,y)
    
    # validation
    X_test = val_combined_cv[features]
    y_test = val_combined_cv['target']
    y_pred = tree_clf.predict(X_test)
    
    print("train_combined_cv : ") 
    print(train_combined_cv)
    print("val_combined_cv : ")
    print(val_combined_cv)
    from sklearn.metrics import classification_report, confusion_matrix
    print(confusion_matrix(y_test, y_pred))
    print(classification_report(y_test,y_pred))
'''

['0.66', '0.69', '0.68', '0.67', '0.66']


'\ncv=KFold(n_splits=3,random_state=5,shuffle=True)\n\ntrain_combined_arr = []\nval_combined_arr = []\n\nfor t,v in cv.split(combined_pd):\n    train_combined_cv=combined_pd.iloc[t]       # 훈련용\n    val_combined_cv=combined_pd.iloc[v]         # 검증용 분리.\n    \n    train_combined_arr.append(train_combined_cv)\n    val_combined_arr.append(val_combined_cv)\n    \n    features = list(train_combined_cv.columns[:-1])\n    X = train_combined_cv[features]\n    y = train_combined_cv[\'target\']\n    tree_clf.fit(X,y)\n    \n    # validation\n    X_test = val_combined_cv[features]\n    y_test = val_combined_cv[\'target\']\n    y_pred = tree_clf.predict(X_test)\n    \n    print("train_combined_cv : ") \n    print(train_combined_cv)\n    print("val_combined_cv : ")\n    print(val_combined_cv)\n    from sklearn.metrics import classification_report, confusion_matrix\n    print(confusion_matrix(y_test, y_pred))\n    print(classification_report(y_test,y_pred))\n'

In [96]:
val_XR_cv.head(10)

A        AA       AAA      AAAA      AAAC      AAAG      AAAU  \
492  0.571429  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
493  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
494  1.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
495  0.720930  0.209302  0.069767  0.023256  0.046512  0.000000  0.000000   
496  0.384615  0.038462  0.000000  0.000000  0.000000  0.000000  0.000000   
497  1.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
498  1.000000  0.333333  0.133333  0.000000  0.000000  0.000000  0.133333   
499  1.000000  0.882353  0.764706  0.647059  0.000000  0.058824  0.000000   
500  0.730769  0.153846  0.038462  0.000000  0.000000  0.000000  0.038462   
501  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

          AAC  AACA      AACC  ...  UUGA      UUGC  UUGG  UUGU       UUU  \
492  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.000000   
493  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.954545   
494  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.000000   
495  0.069767   0.0  0.023256  ...   0.0  0.023256   0.0   0.0  0.000000   
496  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.000000   
497  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.000000   
498  0.066667   0.0  0.066667  ...   0.0  0.000000   0.0   0.0  0.000000   
499  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.000000   
500  0.000000   0.0  0.000000  ...   0.0  0.038462   0.0   0.0  0.000000   
501  0.000000   0.0  0.000000  ...   0.0  0.000000   0.0   0.0  0.954545   

     UUUA  UUUC  UUUG      UUUU  target  
492   0.0   0.0   0.0  0.000000     0.0  
493   0.0   0.0   0.0  0.931818     0.0  
494   0.0   0.0   0.0  0.000000     0.0  
495   0.0   0.0   0.0  0.000000     0.0  
496   0.0   0.0   0.0  0.000000     0.0  
497   0.0   0.0   0.0  0.000000     0.0  
498   0.0   0.0   0.0  0.000000     0.0  
499   0.0   0.0   0.0  0.000000     0.0  
500   0.0   0.0   0.0  0.000000     0.0  
501   0.0   0.0   0.0  0.931818     0.0  

[10 rows x 341 columns]